In [ ]:
import datetime as dt
from pathlib import Path
import xarray as xr

In [ ]:
exps = ['historical', 'ssp126', 'ssp370', 'ssp585']  # 'hist-nat', 
vars = ['pr', 'tas', 'tasmax', 'tasmin', 'hurs']
gcms = {
    'MRI':'mri-esm2-0_r1i1p1f1',
    'UKESM':'ukesm1-0-ll_r1i1p1f2',
    'GFDL':'gfdl-esm4_r1i1p1f1',
}


In [ ]:
locs = {
    
    # # Student request
    # 'suffolk': {'lon': 1.057185, 'lat': 52.285113, 'reason': 'student'},
    # 'pontypridd': {'lon': -3.342, 'lat': 51.602, 'reason': 'student'},
    # 'usk': {'lon': -2.75 , 'lat': 51.75, 'reason': 'student'},
    # 'denbigh': {'lon': -3.5 , 'lat': 53.25, 'reason': 'student'},
    # 'larkana': {'lon': 68.20 , 'lat': 27.56, 'reason': 'student'},
    # 'rome': {'lon': 12.4822 , 'lat': 41.8967, 'reason': 'student'},
    # 'tunis': {'lon': 10.1815 , 'lat': 36.8065, 'reason': 'student'},
    # 'fakenham': {'lon': 0.8493 , 'lat': 52.8313, 'reason': 'student'},
    'tokyo': {'lon': 139.5, 'lat': 35.7, 'reason': 'student'},

    # # Heat Wave Hotspots
    # 'islamabad': {'lon': 73.0479, 'lat': 33.6844, 'reason': 'heat waves'},
    # 'phoenix': {'lon': -112.0740, 'lat': 33.4484, 'reason': 'heat waves'},
    # 'delhi': {'lon': 77.1025, 'lat': 28.7041, 'reason': 'heat waves'},
    # 'baghdad': {'lon': 44.3661, 'lat': 33.3152, 'reason': 'heat waves'},
    # 'athens': {'lon': 23.7275, 'lat': 37.9838, 'reason': 'heat waves'},
    # 'shanghai': {'lon': 121.4737, 'lat': 31.2304, 'reason': 'heat waves and humidity extremes'},

    # # High Precipitation Extremes
    # 'mumbai': {'lon': 72.8777, 'lat': 19.0760, 'reason': 'monsoonal precipitation extremes'},
    # 'jakarta': {'lon': 106.8456, 'lat': -6.2088, 'reason': 'coastal flooding and precipitation extremes'},
    # 'new_orleans': {'lon': -90.0715, 'lat': 29.9511, 'reason': 'hurricane precipitation and sea level rise'},
    # 'dhaka': {'lon': 90.4125, 'lat': 23.8103, 'reason': 'monsoonal precipitation and flood risks'},

    # 'lhr': {'lon': -0.4551, 'lat': 51.4680, 'reason': 'has obs data'},  # London Heathrow
}

In [ ]:
def t():
    return dt.datetime.now().strftime("%H:%M:%S")

def td(start):
    return (dt.datetime.now() - start).total_seconds()


t_start = dt.datetime.now()

print(f"{t()} START script")

# prepare point lists once
names = list(locs.keys())
lats  = [locs[n]["lat"] for n in names]
lons  = [locs[n]["lon"] for n in names]

# Xarray paired selection arrays
lat_da = xr.DataArray(lats, dims="name", coords={"name": names})
lon_da = xr.DataArray(lons, dims="name", coords={"name": names})

for gcm, fname in gcms.items():

    t_start_gcm = dt.datetime.now()
    print(f"{t()}  START GCM = {gcm}")

    for var in vars:
        print(f"{t()}   START var = {var}")
    
        for exp in exps:
            print(f"{t()}    START exp = {exp}")
            t_open = dt.datetime.now()
    
            with xr.open_mfdataset(
                f'{gcm}/{var}/{fname}_w5e5_{exp}_{var}_global_daily_*.nc', 
                chunks={'time': -1}
            ) as ds:
    
                print(f"{t()}    open_mfdataset done (took {td(t_open):.1f}s)")
    
                # Multi-point selection
                t_sel_all = dt.datetime.now()
                out = ds[var].sel(
                    lat=lat_da,
                    lon=lon_da,
                    method="nearest"
                ).load()
                print(f"{t()}    multi-point sel & load done (took {td(t_sel_all):.1f}s)")
    
                # Point-by-point extraction and writing
                for name in names:
                    print(f"{t()}      point = {name}")
                    t_one = dt.datetime.now()
    
                    tas = out.sel(name=name)
    
                    odir = f"../timeseries/{name}/netcdf/{var}/"
                    Path(odir).mkdir(parents=True, exist_ok=True)
    
                    outpath = (
                        f"{odir}/{fname}_w5e5_{exp}_{var}_{name}_daily.nc"
                    )
                    tas.to_netcdf(outpath)
    
                    # print(f"{t()}      write netcdf done (took {td(t_one):.2f}s)")
    
            print(f"{t()}    END exp = {exp}  (total {td(t_open):.1f}s)")
    
        # CSV conversion
        print(f"{t()}   CSV conversion for GCM {gcm} var = {var}")
    
        for name in names:
            idir = f"../timeseries/{name}/netcdf/{var}/"
            odir = f"../timeseries/{name}/csv/{var}/"
            Path(odir).mkdir(parents=True, exist_ok=True)
    
            for exp in exps:
                t_csv = dt.datetime.now()
    
                da = xr.open_dataarray(
                    f"{idir}/{fname}_w5e5_{exp}_{var}_{name}_daily.nc"
                )
                da.to_dataframe().to_csv(
                    f"{odir}/{fname}_w5e5_{exp}_{var}_{name}_daily.csv"
                )
    
                # print(f"{t()}    CSV {name} {exp} done (took {td(t_csv):.2f}s)")
    
        print(f"{t()}   END var = {var}")

    print(f"{t()}  END GCM {gcm} (total {td(t_start_gcm):.2f}s)")
print(f"{t()} END script (total {td(t_start):.2f}s)")

01:08:55 START script
01:08:55  START GCM = MRI
01:08:55  START var = pr
01:08:55    START exp = historical
01:08:56    open_mfdataset done (took 0.9s)


In [22]:
print('Done')

Done
